## Name :- Darpan Gaur
## Roll Number :- CO21BTECH11004

In [1]:
# import libraries
import numpy as np
import matplotlib as mpl
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
from IPython.display import display, HTML
import ipywidgets as widgets
import os

In [2]:
# Fix animation limit to 100MB
mpl.rcParams['animation.embed_limit'] = 100

In [3]:
# Parameters
c_alpha = 0.0
c_beta = 1.0
A_alpha = 1.0
A_beta = 1.0
B_alpha = 2.5
B_beta = 4.5
omega = 1.0

K_phi = 1.0
K_c = 1.0

# domain
N = 512
dx = 1.0
k1, k2, k3=8, 16, 12
x = np.linspace(0, N*dx, N)

# mobility constants
L = 1.0
M = 1.0

# time step
num_steps = 5000
dt = 0.01

In [4]:
# governing equation and derivatives
# f_alpha, f_beta
def f_(c, A_, c_, B_):
    '''
    $f_ = A_(c - c_)^2 + B_$
    '''
    return A_ * (c - c_)**2 + B_

# h_phi
def h_phi(phi):
    '''
    $ h(\phi) = \phi^3 * (10 - 15 * \phi + 6 * \phi^2) $
    '''
    return phi**3 * (10 - 15 * phi + 6 * phi**2)

def f_c_phi(c, phi, omega):
    '''
    $ f_c_phi = (1-h_phi(phi)) * f_(c, A_alpha, c_alpha, B_alpha) + h_phi(phi) * f_(c, A_beta, c_beta, B_beta) + omega * phi^2 * (1 - phi)^2 $
    '''
    return (1 - h_phi(phi)) * f_(c, A_alpha, c_alpha, B_alpha) + h_phi(phi) * f_(c, A_beta, c_beta, B_beta) + omega * phi**2 * (1 - phi)**2

def df_dphi(c, phi, omega):
    dh_dphi = 30 * phi**2 * (phi - 1)**2
    return dh_dphi * (f_(c, A_beta, c_beta, B_beta) - f_(c, A_alpha, c_alpha, B_alpha)) + 2 * omega * phi * (1 - phi) * (1 - 2 * phi)

def df_dc(c, phi, omega):
    return (1-h_phi(phi)) * 2 * A_alpha * (c - c_alpha) + h_phi(phi) * 2 * A_beta * (c - c_beta)

In [5]:
# laplacian_1d
def laplacian_1d(phi, dx):
    return (np.roll(phi, -1) + np.roll(phi, 1) - 2 * phi) / dx**2

In [6]:
def solve(c, phi, num_steps, plot_every):
    c_snapshots = []
    phi_snapshots = []

    c_snapshots.append(c.copy())
    phi_snapshots.append(phi.copy())

    for step in range(num_steps):
        lap_c = laplacian_1d(c, dx)
        mu = df_dc(c, phi, omega) - 2 * K_c * lap_c
        c += dt * M * laplacian_1d(mu, dx)

        lap_phi = laplacian_1d(phi, dx)
        phi += dt * L * (2 * K_phi * lap_phi - df_dphi(c, phi, omega))

        if step % plot_every == 0:
            c_snapshots.append(c.copy())
            phi_snapshots.append(phi.copy())

    return c_snapshots, phi_snapshots

In [7]:
c0 = [0.0, 0.3, 0.7]
for c_ in c0:
    c = np.full(N, c_)
    phi = np.zeros(N)
    c[N//4-k1:N//4+k1] = 1.0
    phi[N//4-k1:N//4+k1] = 1.0

    c[N//2-k2:N//2+k2] = 1.0
    phi[N//2-k2:N//2+k2] = 1.0

    c[3*N//4-k3:3*N//4+k3] = 1.0
    phi[3*N//4-k3:3*N//4+k3] = 1.0
    

    c_snapshots, phi_snapshots = solve(c, phi, num_steps, 100)

    fig, ax = plt.subplots(figsize=(10, 5))
    c_plot = ax.plot(x, c_snapshots[0], 'b-', lw=2, label='c')
    phi_plot = ax.plot(x, phi_snapshots[0], 'r-', lw=2, label='$\phi$')
    ax.set_xlabel('x')
    ax.legend()
    ax.set_title(f'Coupled Allen Cahn and Cahn Hillard problem: c0 = {c_}') 

    def update(frame):
        c_plot[0].set_ydata(c_snapshots[frame])
        phi_plot[0].set_ydata(phi_snapshots[frame])
        return c_plot, phi_plot
    
    anim = FuncAnimation(fig, update, frames=len(c_snapshots), interval=100, blit=False)
    plt.close()

    display(HTML(anim.to_jshtml()))
    